In [1]:
# Load the required libraries
import pandas as pd
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import nltk
from nltk.corpus import wordnet
from nltk import pos_tag
import numpy as np
from spellchecker import SpellChecker
import nltk
from nltk.corpus import stopwords



nltk.download('averaged_perceptron_tagger')


# Ensure that necessary NLTK resources are available
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')


[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/anachkhaidze/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/anachkhaidze/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/anachkhaidze/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/anachkhaidze/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [2]:
# Adjust display options
pd.set_option('display.max_columns', None)  # None means no limit

In [3]:
# Load the CSV files into Pandas DataFrames
hallucinations_df = pd.read_csv('data/hallucinations.csv')
lancaster_df = pd.read_csv('norms/lancaster.csv')

# Rename the specified variable in the hallucinations dataset
hallucinations_df.rename(columns={'Please describe as much as you can remember about what you saw in the Ganzflicker:': 'hallucination_description'}, inplace=True)
hallucinations_df.rename(columns={'What is your gender?': 'gender'}, inplace=True)
hallucinations_df.rename(columns={'How old are you?': 'age'}, inplace=True)
hallucinations_df.rename(columns={'How would you describe your VISUAL imagery vividness on a scale from 0-10?': 'visual_vividness'}, inplace=True)
hallucinations_df.rename(columns={'How long did you view the Ganzflicker?': 'view_duration'}, inplace=True)
hallucinations_df.rename(columns={'Did you view the Ganzflicker with the lights in the room turned off?': 'lights'}, inplace=True)
hallucinations_df.rename(columns={'Did you view the Ganzflicker on a computer or mobile phone?': 'computer'}, inplace=True)
hallucinations_df.rename(columns={'How did you find the experience emotionally?': 'emotion'}, inplace=True)
hallucinations_df.rename(columns={'Did you see anything in the Ganzflicker? If not, confirm by answering "no" and then skip to the next section.': 'hallucination_categorical'}, inplace=True)
hallucinations_df.rename(columns={'About how long did it take before images started to emerge?': 'emerge_time'}, inplace=True)
hallucinations_df.rename(columns={'About how frequently did you experience images?': 'hallucination_frequency'}, inplace=True)
hallucinations_df.rename(columns={'If you saw images, how intense were they?': 'hallucination_intensity'}, inplace=True)
hallucinations_df.rename(columns={'If you saw images, how long did a single image last?': 'hallucination_duration'}, inplace=True)
hallucinations_df.rename(columns={'How did your normal state of consciousness change during the experience?': 'consciousness_change'}, inplace=True)
hallucinations_df.rename(columns={'If you felt a change in your state of consciousness, please describe how you felt in more detail:': 'consciousness_description'}, inplace=True)
hallucinations_df.rename(columns={'If you saw images, where did they tend to appear on the screen?': 'hallucination_location'}, inplace=True)


In [4]:
hallucinations_df

id      gender  age  visual_vividness     view_duration lights  \
0        1      Female   21                 3  Less than 10min.    Yes   
1        2        Male  NaN                 3            10min.    Yes   
2        3        Male   26                 8            10min.     No   
3        4      Female   42                 0            10min.    Yes   
4        5        Male  NaN                 8            10min.    Yes   
...    ...         ...  ...               ...               ...    ...   
4360  4361      Female   31                 6            10min.    Yes   
4361  4362        Male   30                 8    Didn't time it    Yes   
4362  4363      Female   34                10            10min.    Yes   
4363  4364      Female   63                 8    Didn't time it    Yes   
4364  4365  Non-binary   11                 8  Less than 10min.    Yes   

          computer                                        emotion  \
0         Computer                  Unpleasant, wanted it to stop   
1         Computer           Somewhat enjoyable, but easy to stop   
2         Computer           Somewhat enjoyable, but easy to stop   
3         Computer  Somewhat unpleasant, but didn't mind going on   
4         Computer           Somewhat enjoyable, but easy to stop   
...            ...                                            ...   
4360      Computer  Somewhat unpleasant, but didn't mind going on   
4361      Computer  Somewhat unpleasant, but didn't mind going on   
4362  Mobile phone  Somewhat unpleasant, but didn't mind going on   
4363  Mobile phone           Somewhat enjoyable, but easy to stop   
4364      Computer                  Unpleasant, wanted it to stop   

                              hallucination_categorical  \
0     Simple shapes or patterns (e.g., ball of light...   
1     Simple shapes or patterns (e.g., ball of light...   
2     Complex objects (e.g., animals, faces, buildings)   
3     Distortions (e.g., screen warping or rotating)...   
4     Simple shapes or patterns (e.g., ball of light...   
...                                                 ...   
4360  Simple shapes or patterns (e.g., ball of light...   
4361  Simple shapes or patterns (e.g., ball of light...   
4362  Simple shapes or patterns (e.g., ball of light...   
4363  Simple shapes or patterns (e.g., ball of light...   
4364  Simple shapes or patterns (e.g., ball of light...   

                              hallucination_description  \
0                      alien bust  , skull , butterfly    
1       blach rectangular shapes flashing on the screen   
2                          corridor with bright windows   
3      different vague patterns, pulsing, the image ...   
4     geometric patterns, as seen in 2D FFT output g...   
...                                                 ...   
4360  yellow orbs or streaks of light that were purp...   
4361  Yellows and Greens at the peripheral edges. Mo...   
4362  You know how when they record music they have ...   
4363                              Zebra oval ball spots   
4364  Zooming into a grid of shapes, faces twisted i...   

                           emerge_time  \
0                        A few seconds   
1                          1-2 minutes   
2                          1-2 minutes   
3                          1-2 minutes   
4                          1-2 minutes   
...                                ...   
4360                     A few seconds   
4361  They began to emerge immediately   
4362                     A few seconds   
4363                       1-2 minutes   
4364                     A few seconds   

                         hallucination_frequency  \
0                                     Constantly   
1                                     Frequently   
2                                     Frequently   
3     I saw patterns consistently, but no images   
4                                     Frequently   
...                                          ...   
436

In [9]:
# Preprocess lancaster_df to lowercase the 'Word' column
lancaster_df['Word'] = lancaster_df['Word'].str.lower()

# Set 'Word' as the index for easier lookup
lancaster_df.set_index('Word', inplace=True)

# Initialize the spell checker
spell = SpellChecker()

def autocorrect_words(words):
    # Use the spell checker to correct the words
    corrected_words = [spell.correction(word) for word in words]
    print("Corrected words:", corrected_words)
    # Filter out None values returned by spell checker
    corrected_words = [word for word in corrected_words if word is not None]
    print("Filtered corrected words:", corrected_words)
    return corrected_words


# Initialize the NLTK lemmatizer
lemmatizer = WordNetLemmatizer()

# Modify the nltk_tag_to_wordnet_tag function to default to NOUN
def nltk_tag_to_wordnet_tag(nltk_tag):
    if nltk_tag.startswith('J'):
        return wordnet.ADJ
    elif nltk_tag.startswith('V'):
        return wordnet.VERB
    elif nltk_tag.startswith('N'):
        return wordnet.NOUN
    elif nltk_tag.startswith('R'):
        return wordnet.ADV
    else:          
        return wordnet.NOUN  # Default to noun if the tag is not recognized

# Modify the lemmatize_text function to ensure words are lemmatized to their singular form
def lemmatize_text(tokens):
    # Lowercase all tokens
    tokens = [word.lower() for word in tokens]
    # Lemmatize words
    lemmatizer = WordNetLemmatizer()
    print("Tokens before lemmatization:", tokens)
    lemmatized_words = [lemmatizer.lemmatize(word) for word in tokens if lemmatizer.lemmatize(word) is not None]
    print("Tokens after lemmatization:", lemmatized_words)
    return lemmatized_words

# Define the list of English stopwords
stop_words = set(stopwords.words('english'))
# Add additional stopwords
additional_stopwords = ['screen', 'saw', 'screens', 'screened']

# Initialize the spell checker
spell = SpellChecker()

# Initialize the lemmatizer
lemmatizer = WordNetLemmatizer()

def preprocess_text(text):
    # Tokenize the text
    tokens = nltk.word_tokenize(text)
    # Remove punctuation and lowercase all tokens
    tokens = [word.lower() for word in tokens if word.isalpha()]
    # Remove 'screen' and 'saw' from tokens
    tokens = [word for word in tokens if word not in stop_words and word not in additional_stopwords]
    # Lemmatize words
    lemmatizer = WordNetLemmatizer()
    print("Tokens before lemmatization:", tokens)
    # Filter out None values returned by lemmatizer
    tokens = [lemmatizer.lemmatize(word) for word in tokens if lemmatizer.lemmatize(word) is not None]
    print("Tokens after lemmatization:", tokens)
    return tokens

# Apply the preprocessing function to the hallucination_description column
hallucinations_df['hallucination_description'] = hallucinations_df['hallucination_description'].apply(preprocess_text)

# Define the categories to calculate averages for
categories = ['Auditory.mean', 'Gustatory.mean', 'Haptic.mean', 'Interoceptive.mean',
              'Olfactory.mean', 'Visual.mean', 'Foot_leg.mean', 'Hand_arm.mean',
              'Head.mean', 'Mouth.mean', 'Torso.mean', 'Max_strength.perceptual',
              'Max_strength.action', 'Max_strength.sensorimotor']

def calculate_means_and_missing(description, lancaster_df, categories):
    # Lemmatize the corrected words
    lemmatized_words = lemmatize_text(description)
    
    # Initialize sums, counts, and missing word count
    category_sums = {category: 0 for category in categories}
    category_counts = {category: 0 for category in categories}
    missing_words_count = 0
    
    # Count the values and track missing words
    for word in lemmatized_words:
        if word in lancaster_df.index:
            for category in categories:
                value = lancaster_df.at[word, category]
                if pd.notnull(value):
                    category_sums[category] += value
                    category_counts[category] += 1
        else:
            missing_words_count += 1
    
    # Calculate the average for each category
    category_means = {category: (category_sums[category] / category_counts[category] if category_counts[category] > 0 else 0) for category in categories}
    
    # Calculate the percentage of missing words
    total_words_count = len(lemmatized_words)
    percent_missing = (missing_words_count / total_words_count * 100) if total_words_count > 0 else 0
    
    return category_means, percent_missing

# Apply the function to each row in hallucinations_df['hallucination_description']
results = hallucinations_df['hallucination_description'].apply(
    lambda desc: calculate_means_and_missing(desc, lancaster_df, categories)
)

# Split the results into separate columns
hallucinations_df['category_means'] = results.apply(lambda x: x[0])
hallucinations_df['percent_missing'] = results.apply(lambda x: x[1])

# Separate the category means into individual columns
for category in categories:
    hallucinations_df[category] = hallucinations_df['category_means'].apply(lambda means: means[category])

# Drop the temporary 'category_means' column if it's no longer needed
hallucinations_df.drop('category_means', axis=1, inplace=True)

# Check the result
print(hallucinations_df[['percent_missing'] + categories].head())


Tokens before lemmatization: ['alien', 'bust', 'skull', 'butterfly']
Tokens after lemmatization: ['alien', 'bust', 'skull', 'butterfly']
Tokens before lemmatization: ['blach', 'rectangular', 'shapes', 'flashing']
Tokens after lemmatization: ['blach', 'rectangular', 'shape', 'flashing']
Tokens before lemmatization: ['corridor', 'bright', 'windows']
Tokens after lemmatization: ['corridor', 'bright', 'window']
Tokens before lemmatization: ['different', 'vague', 'patterns', 'pulsing', 'image', 'shifted', 'mostly', 'yellow', 'mostly', 'black']
Tokens after lemmatization: ['different', 'vague', 'pattern', 'pulsing', 'image', 'shifted', 'mostly', 'yellow', 'mostly', 'black']
Tokens before lemmatization: ['geometric', 'patterns', 'seen', 'fft', 'output', 'given', 'luminance', 'modulation', 'input', 'emphasizing', 'vertical', 'horizontal', 'orientations']
Tokens after lemmatization: ['geometric', 'pattern', 'seen', 'fft', 'output', 'given', 'luminance', 'modulation', 'input', 'emphasizing', 've

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Tokens before lemmatization: ['clusters', 'grids', 'background', 'evocative', 'flames', 'bonfire']
Tokens after lemmatization: ['cluster', 'grid', 'background', 'evocative', 'flame', 'bonfire']
Tokens before lemmatization: ['color', 'changing', 'white', 'yellow']
Tokens after lemmatization: ['color', 'changing', 'white', 'yellow']
Tokens before lemmatization: ['color', 'started', 'morphed', 'blue', 'geometric', 'shapes', 'sharp', 'angles', 'appeared', 'well', 'swirls', 'constantly', 'moving', 'eyes', 'shut', 'different', 'geometric', 'shapes', 'shades', 'gray']
Tokens after lemmatization: ['color', 'started', 'morphed', 'blue', 'geometric', 'shape', 'sharp', 'angle', 'appeared', 'well', 'swirl', 'constantly', 'moving', 'eye', 'shut', 'different', 'geometric', 'shape', 'shade', 'gray']
Tokens before lemmatization: ['color', 'variations', 'edge', 'whole', 'blobs', 'green', 'blue', 'almost', 'like', 'image']
Tokens after lemmatization: ['color', 'variation', 'edge', 'whole', 'blob', 'gree

Tokens before lemmatization: ['flicker', 'seemed', 'speed', 'images', 'lasted', 'seconds', 'faint', 'object', 'near', 'centre', 'later', 'negative', 'bust', 'man', 'long', 'wig', 'period', 'costume', 'eyelids', 'drooped', 'background', 'changed', 'dark', 'blue', 'fine', 'waving', 'lines', 'mostly', 'bottom', 'blinked', 'flicker', 'reverted', 'red', 'black', 'later', 'regular', 'patterns', 'images', 'like', 'wallpaper', 'became', 'like', 'penguins', 'toward', 'end', 'patterns', 'less', 'discernible', 'closer', 'together']
Tokens after lemmatization: ['flicker', 'seemed', 'speed', 'image', 'lasted', 'second', 'faint', 'object', 'near', 'centre', 'later', 'negative', 'bust', 'man', 'long', 'wig', 'period', 'costume', 'eyelid', 'drooped', 'background', 'changed', 'dark', 'blue', 'fine', 'waving', 'line', 'mostly', 'bottom', 'blinked', 'flicker', 'reverted', 'red', 'black', 'later', 'regular', 'pattern', 'image', 'like', 'wallpaper', 'became', 'like', 'penguin', 'toward', 'end', 'pattern', 

Tokens after lemmatization: ['mainly', 'remember', 'rainbow', 'streak', 'tree', 'think', 'rainbow', 'either', 'really', 'bright', 'pretty', 'subtle']
Tokens before lemmatization: ['mainly', 'pastel', 'colors', 'addition', 'red', 'black']
Tokens after lemmatization: ['mainly', 'pastel', 'color', 'addition', 'red', 'black']
Tokens before lemmatization: ['managed', 'almost', 'minutes', 'painful', 'eyes', 'continue', 'quite', 'dynamic', 'small', 'bigger', 'shapes', 'patterns', 'emerging', 'moving', 'across', 'small', 'colored', 'squares', 'rhombuses', 'etc', 'starting', 'tiny', 'growing', 'size', 'reddish', 'patterns', 'sweeping', 'like', 'wave', 'across', 'gathering', 'middle', 'verticle', 'lines', 'interesting', 'really', 'painful', 'eyes']
Tokens after lemmatization: ['managed', 'almost', 'minute', 'painful', 'eye', 'continue', 'quite', 'dynamic', 'small', 'bigger', 'shape', 'pattern', 'emerging', 'moving', 'across', 'small', 'colored', 'square', 'rhombus', 'etc', 'starting', 'tiny', 'g

...

Tokens before lemmatization: ['simple', 'shape', 'line', 'slash', 'one', 'occasion', 'face', 'rudimentary', 'almost', 'demon', 'pure', 'black', 'horn', 'hole', 'eye', 'mouth', 'hole']
Tokens after lemmatization: ['simple', 'shape', 'line', 'slash', 'one', 'occasion', 'face', 'rudimentary', 'almost', 'demon', 'pure', 'black', 'horn', 'hole', 'eye', 'mouth', 'hole']
Tokens before lemmatization: ['simple', 'shape', 'brief', 'period']
Tokens after lemmatization: ['simple', 'shape', 'brief', 'period']
Tokens before lemmatization: ['simple', 'shape', 'pattern', 'ball', 'light', 'line', 'grid', 'spiderwebs', 'geometric', 'shape']
Tokens after lemmatization: ['simple', 'shape', 'pattern', 'ball', 'light', 'line', 'grid', 'spiderwebs', 'geometric', 'shape']
Tokens before lemmatization: ['simple', 'shape', 'pattern', 'distortion']
Tokens after lemmatization: ['simple', 'shape', 'pattern', 'distortion']
Tokens before lemmatization: ['simple', 'shape', 'cube', 'grid', 'color', 'blue', 'green']
Tok

Tokens before lemmatization: ['started', 'flicker', 'color', 'change', 'white', 'green', 'shape', 'flicker', 'circle', 'mostly', 'morphing', 'point', 'seemed', 'expand', 'beyond', 'monitor']
Tokens after lemmatization: ['started', 'flicker', 'color', 'change', 'white', 'green', 'shape', 'flicker', 'circle', 'mostly', 'morphing', 'point', 'seemed', 'expand', 'beyond', 'monitor']
Tokens before lemmatization: ['started', 'palm', 'tree', 'several', 'spot', 'changed', 'looked', 'like', 'riding', 'car', 'forest', 'canopy', 'looked', 'like', 'water', 'looking', 'line', 'following', 'began', 'look', 'like', 'riding', 'tunnel', 'fast', 'speed']
Tokens after lemmatization: ['started', 'palm', 'tree', 'several', 'spot', 'changed', 'looked', 'like', 'riding', 'car', 'forest', 'canopy', 'looked', 'like', 'water', 'looking', 'line', 'following', 'began', 'look', 'like', 'riding', 'tunnel', 'fast', 'speed']
Tokens before lemmatization: ['started', 'seeing', 'stripe', 'like', 'thing', 'diagonally', 's

Tokens after lemmatization: ['flickering', 'center', 'appeared', 'sync', 'rest', 'flicker', 'flickering', 'grid', 'concentric', 'circle', 'line', 'radiating', 'center']
Tokens before lemmatization: ['flicker', 'would', 'change', 'speed', 'dark', 'area', 'would', 'go']
Tokens after lemmatization: ['flicker', 'would', 'change', 'speed', 'dark', 'area', 'would', 'go']
Tokens before lemmatization: ['geometric', 'shape', 'line', 'began', 'immediately', 'followed', 'simple', 'butterfly', 'star', 'pattern', 'started', 'get', 'detailed', 'purple', 'white', 'first', 'color', 'followed', 'hint', 'blue', 'green', 'burst', 'light', 'spinning', 'twisting', 'distortion', 'flashing', 'began', 'move', 'around', 'corner', 'laptop', 'coming', 'felt', 'incredibly', 'started', 'see', 'outline', 'object', 'people', 'building', 'could', 'see', 'face', 'complete', 'colored', 'detail', 'strong', 'outline', 'first', 'large', 'shooting', 'star', 'outline', 'high', 'rise', 'building', 'window', 'also', 'kept', '

Tokens before lemmatization: ['first', 'mountain', 'forming', 'middle', 'started', 'erupting', 'like', 'volcano', 'lava', 'starting', 'flowing', 'filling', 'forming', 'image', 'lot', 'pattern', 'like', 'one', 'certain', 'type', 'tile', 'morphed', 'changed', 'image', 'mountain', 'volcano', 'come', 'back', 'several', 'point', 'quite', 'kind', 'vivid', 'real', 'landscape', 'would', 'vivid', 'like', 'cartoon', 'caricature', 'drawing', 'lot', 'blue', 'purple']
Tokens after lemmatization: ['first', 'mountain', 'forming', 'middle', 'started', 'erupting', 'like', 'volcano', 'lava', 'starting', 'flowing', 'filling', 'forming', 'image', 'lot', 'pattern', 'like', 'one', 'certain', 'type', 'tile', 'morphed', 'changed', 'image', 'mountain', 'volcano', 'come', 'back', 'several', 'point', 'quite', 'kind', 'vivid', 'real', 'landscape', 'would', 'vivid', 'like', 'cartoon', 'caricature', 'drawing', 'lot', 'blue', 'purple']
Tokens before lemmatization: ['beginning', 'ganzflicker', 'green', 'spiral', 'beg

Tokens before lemmatization: ['white', 'orb', 'like', 'number', 'red', 'dice', 'defined']
Tokens after lemmatization: ['white', 'orb', 'like', 'number', 'red', 'dice', 'defined']
Tokens before lemmatization: ['white', 'ray', 'looking', 'like', 'turning', 'around', 'mandelbrot', 'set', 'zoom', 'faint', 'tree', 'forest', 'bottom']
Tokens after lemmatization: ['white', 'ray', 'looking', 'like', 'turning', 'around', 'mandelbrot', 'set', 'zoom', 'faint', 'tree', 'forest', 'bottom']
Tokens before lemmatization: ['white', 'rose', 'getting', 'bigger', 'smaller']
Tokens after lemmatization: ['white', 'rose', 'getting', 'bigger', 'smaller']
Tokens before lemmatization: ['white', 'shape', 'like', 'cell', 'slowly', 'moving', 'around', 'center', 'image', 'area']
Tokens after lemmatization: ['white', 'shape', 'like', 'cell', 'slowly', 'moving', 'around', 'center', 'image', 'area']
Tokens before lemmatization: ['whitish', 'bluish', 'rotating', 'triangle', 'center', 'red', 'black', 'blue', 'flickering

In [10]:
hallucinations_df

id      gender  age  visual_vividness     view_duration lights  \
0        1      Female   21                 3  Less than 10min.    Yes   
1        2        Male  NaN                 3            10min.    Yes   
2        3        Male   26                 8            10min.     No   
3        4      Female   42                 0            10min.    Yes   
4        5        Male  NaN                 8            10min.    Yes   
...    ...         ...  ...               ...               ...    ...   
4360  4361      Female   31                 6            10min.    Yes   
4361  4362        Male   30                 8    Didn't time it    Yes   
4362  4363      Female   34                10            10min.    Yes   
4363  4364      Female   63                 8    Didn't time it    Yes   
4364  4365  Non-binary   11                 8  Less than 10min.    Yes   

          computer                                        emotion  \
0         Computer                  Unpleasant, wanted it to stop   
1         Computer           Somewhat enjoyable, but easy to stop   
2         Computer           Somewhat enjoyable, but easy to stop   
3         Computer  Somewhat unpleasant, but didn't mind going on   
4         Computer           Somewhat enjoyable, but easy to stop   
...            ...                                            ...   
4360      Computer  Somewhat unpleasant, but didn't mind going on   
4361      Computer  Somewhat unpleasant, but didn't mind going on   
4362  Mobile phone  Somewhat unpleasant, but didn't mind going on   
4363  Mobile phone           Somewhat enjoyable, but easy to stop   
4364      Computer                  Unpleasant, wanted it to stop   

                              hallucination_categorical  \
0     Simple shapes or patterns (e.g., ball of light...   
1     Simple shapes or patterns (e.g., ball of light...   
2     Complex objects (e.g., animals, faces, buildings)   
3     Distortions (e.g., screen warping or rotating)...   
4     Simple shapes or patterns (e.g., ball of light...   
...                                                 ...   
4360  Simple shapes or patterns (e.g., ball of light...   
4361  Simple shapes or patterns (e.g., ball of light...   
4362  Simple shapes or patterns (e.g., ball of light...   
4363  Simple shapes or patterns (e.g., ball of light...   
4364  Simple shapes or patterns (e.g., ball of light...   

                              hallucination_description  \
0                       [alien, bust, skull, butterfly]   
1                 [blach, rectangular, shape, flashing]   
2                            [corridor, bright, window]   
3     [different, vague, pattern, pulsing, image, sh...   
4     [geometric, pattern, seen, fft, output, given,...   
...                                                 ...   
4360  [yellow, orb, streak, light, purple, edge, wou...   
4361  [yellow, green, peripheral, edge, morphing, ge...   
4362  [know, record, music, control, light, show, di...   
4363                          [zebra, oval, ball, spot]   
4364  [zooming, grid, shape, face, twisted, cruel, s...   

                           emerge_time  \
0                        A few seconds   
1                          1-2 minutes   
2                          1-2 minutes   
3                          1-2 minutes   
4                          1-2 minutes   
...                                ...   
4360                     A few seconds   
4361  They began to emerge immediately   
4362                     A few seconds   
4363                       1-2 minutes   
4364                     A few seconds   

                         hallucination_frequency  \
0                                     Constantly   
1                                     Frequently   
2                                     Frequently   
3     I saw patterns consistently, but no images   
4                                     Frequently   
...                                          ...   
436

In [11]:
# # Calculate the average percent_missing
# average_percent_missing = hallucinations_df['percent_missing'].mean()

# print("Average percent_missing:", average_percent_missing)

In [12]:
hallucinations_df.rename(columns={'Max_strength.perceptual': 'perceptual_strength'}, inplace=True)
hallucinations_df.rename(columns={'Max_strength.action': 'action_strength'}, inplace=True)
hallucinations_df.rename(columns={'Max_strength.sensorimotor': 'sensorimotor_strength'}, inplace=True)
hallucinations_df.rename(columns={'Visual.mean': 'visual_strength'}, inplace=True)
hallucinations_df.rename(columns={'Interoceptive.mean': 'interoceptive_strength'}, inplace=True)
hallucinations_df.rename(columns={'Auditory.mean': 'auditory_strength'}, inplace=True)
hallucinations_df.rename(columns={'Gustatory.mean': 'gustatory_strength'}, inplace=True)
hallucinations_df.rename(columns={'Haptic.mean': 'haptic_strength'}, inplace=True)
hallucinations_df.rename(columns={'Interoceptive.mean': 'interoceptive_strength'}, inplace=True)
hallucinations_df.rename(columns={'Olfactory.mean': 'olfactory_strength'}, inplace=True)
hallucinations_df.rename(columns={'Foot_leg.mean': 'foot_strength'}, inplace=True)
hallucinations_df.rename(columns={'Hand_arm.mean': 'hand_strength'}, inplace=True)
hallucinations_df.rename(columns={'Head.mean': 'head_strength'}, inplace=True)
hallucinations_df.rename(columns={'Torso.mean': 'torso_strength'}, inplace=True)
hallucinations_df.rename(columns={'Mouth.mean': 'mouth_strength'}, inplace=True)

In [13]:
# Z_score visual vividness scores

hallucinations_df['visual_vividness_z'] = (hallucinations_df['visual_vividness'] - hallucinations_df['visual_vividness'].mean()) / hallucinations_df['visual_vividness'].std()

In [14]:
# Function to calculate the length of the list of words in each row
def calculate_description_length(tokens):
    return len(tokens)

# Apply the function to each row in 'hallucination_description' and create a new column 'description_length'
hallucinations_df['description_length'] = hallucinations_df['hallucination_description'].apply(calculate_description_length)


In [79]:
# # Calculate the first quartile (Q1)
# Q1 = hallucinations_df['description_length'].quantile(0.25)

# # Calculate the third quartile (Q3)
# Q3 = hallucinations_df['description_length'].quantile(0.75)

# # Calculate the interquartile range (IQR)
# IQR = Q3 - Q1

# # Define the lower and upper bounds for outliers detection
# lower_bound = Q1 - 1.5 * IQR

# Filter the DataFrame to remove outliers
hallucinations_df_filtered = hallucinations_df[(hallucinations_df['description_length'] >= 3)]

In [82]:
# hallucinations_df_filtered.to_csv('data/hallucinations_df_for_r.csv', index=False)